In [1]:
from recpack.datasets import AdressaOneWeek, CosmeticsShop, RecsysChallenge2015
from recpack.scenarios import Timed
from recpack.pipelines import PipelineBuilder
from recpack.algorithms import TARSItemKNN

In [2]:
import datetime

In [3]:
DATASET_PATH = '/Users/robinverachtert/workspace/doctorate/datasets/'

In [4]:
datasets = {
    'adressa': {
        'dataset': AdressaOneWeek(path=DATASET_PATH, filename='adressa.csv'),
        't': int(datetime.datetime(2017, 1, 7, 12).strftime('%s')),
        't_val': int(datetime.datetime(2017, 1, 6, 12).strftime('%s')),
        'delta_out': 12*3600,
    },
    'cosmeticsshop': {
        'dataset': CosmeticsShop(path=DATASET_PATH, filename='cosmeticsshop_views.csv'),
        't': int(datetime.datetime(2020, 2, 15, 0).strftime('%s')),
        't_val': int(datetime.datetime(2020, 2, 1, 0).strftime('%s')),
        'delta_out': 14*24*3600,
    },
    'recsys2015': {
        'dataset': RecsysChallenge2015(path=DATASET_PATH, filename='yoochoose-clicks.dat'),
        't': int(datetime.datetime(2014, 9, 15, 0).strftime('%s')),
        't_val': int(datetime.datetime(2014, 9, 1, 0).strftime('%s')),
        'delta_out': 14*24*3600,
    }
} 

In [13]:
DATASET = 'cosmeticsshop'

im = datasets[DATASET]['dataset'].load()
t = datasets[DATASET]['t']
t_val = datasets[DATASET]['t_val']
delta_out = datasets[DATASET]['delta_out']

  0%|          | 0/7877677 [00:00<?, ?it/s]

  0%|          | 0/7877677 [00:00<?, ?it/s]

In [14]:
scenario = Timed(t=t, t_validation=t_val, delta_out=delta_out, validation=True)
scenario.split(im)

In [15]:
builder = PipelineBuilder(f'experiment_{DATASET}')
builder.set_data_from_scenario(scenario)
builder.set_optimisation_metric('NDCGK', 10)
builder.add_metric('NDCGK', [10, 20, 50])
builder.add_metric('CoverageK', [10, 20])

# Existing Papers
builder.add_algorithm('TARSItemKNNLee_W3', grid={'similarity': ['cosine', 'pearson']})
builder.add_algorithm('TARSItemKNNLee_W5', grid={'similarity': ['cosine', 'pearson']})

HOUR = 3600 # seconds
DAY = 24*HOUR

builder.add_algorithm('TARSItemKNNLiu', grid={
    'fit_decay': [1/x for x in [1*HOUR, 2*HOUR, 3*HOUR, 6*HOUR, 12*HOUR, 1*DAY, 7*DAY, 14*DAY]],
    'predict_decay': [1/x for x in [1*HOUR, 2*HOUR, 3*HOUR, 6*HOUR, 12*HOUR, 1*DAY, 7*DAY, 14*DAY]],
})

builder.add_algorithm('TARSItemKNNDing', grid={
    'predict_decay': [1/x for x in [1*HOUR, 2*HOUR, 3*HOUR, 6*HOUR, 12*HOUR, 1*DAY, 7*DAY, 14*DAY]],
    'similarity': ['cosine', 'conditional_probability'],
})

builder.add_algorithm('TARSItemKNNLiu2012', grid={
    'decay': [2, 5, 10, 50, 100, 200, 500, 1000],
})

# Baselines
builder.add_algorithm('ItemKNN', grid={'similarity': ['cosine', 'conditional_probability']})
builder.add_algorithm('Popularity')

# NOVEL COMBINATIONS
builder.add_algorithm('TARSItemKNNLee', grid={'similarity': ['cosine', 'pearson'], 'W': [2, 3, 4, 5, 8, 10, 16]})

builder.add_algorithm(
    'TARSItemKNN', 
    params={'decay_function': 'exponential'},
    grid={
        'similarity': TARSItemKNN.SUPPORTED_SIMILARITIES,
        'K': [10, 50, 100, 200, 500],
        'fit_decay': [1/x for x in [1*HOUR, 2*HOUR, 3*HOUR, 6*HOUR, 12*HOUR, 1*DAY, 7*DAY, 14*DAY]],
        'predict_decay': [1/x for x in [1*HOUR, 2*HOUR, 3*HOUR, 6*HOUR, 12*HOUR, 1*DAY, 7*DAY, 14*DAY]],
    }
)
builder.add_algorithm(
    'TARSItemKNN', 
    params={'decay_function': 'log'},
    grid={
        'similarity': TARSItemKNN.SUPPORTED_SIMILARITIES,
        'K': [10, 50, 100, 200, 500],
        'fit_decay': [2, 4, 8, 16, 32],
        'predict_decay': [2, 4, 8, 16, 32]
    }
)
builder.add_algorithm(
    'TARSItemKNN', 
    params={'decay_function': 'linear'},
    grid={
        'similarity': TARSItemKNN.SUPPORTED_SIMILARITIES,
        'K': [10, 50, 100, 200, 500],
        'fit_decay': [0.1, 0.3, 0.5, 0.7, 0.9, 1],
        'predict_decay': [0.1, 0.3, 0.5, 0.7, 0.9, 1],
    }
)
builder.add_algorithm(
    'TARSItemKNN', 
    params={'decay_function': 'concave'},
    grid={
        'similarity': TARSItemKNN.SUPPORTED_SIMILARITIES,
        'K': [10, 50, 100, 200, 500],
        'fit_decay': [0.01, 0.1, 0.3, 0.9],
        'predict_decay': [0.01, 0.1, 0.3, 0.9]
    }
)
builder.add_algorithm(
    'TARSItemKNN', 
    params={'decay_function': 'convex'},
    grid={
        'similarity': TARSItemKNN.SUPPORTED_SIMILARITIES,
        'K': [10, 50, 100, 200, 500],
        'fit_decay': [0.01, 0.1, 0.3, 0.9],
        'predict_decay': [0.01, 0.1, 0.3, 0.9]
    }
)

builder.add_algorithm(
    'TARSItemKNN', 
    params={'decay_function': 'linear_steeper'},
    grid={
        'similarity': TARSItemKNN.SUPPORTED_SIMILARITIES,
        'K': [10, 50, 100, 200, 500],
        'fit_decay': [0.1, 0.5, 1, 2, 4, 8],
        'predict_decay': [0.1, 0.5, 1, 2, 4, 8],
    }
)

builder.add_algorithm(
    'TARSItemKNNVaz', 
    grid={
        'K': [10, 50, 100, 200, 500],
        'fit_decay': [1/x for x in [1*HOUR, 2*HOUR, 3*HOUR, 6*HOUR, 12*HOUR, 1*DAY, 7*DAY, 14*DAY]],
        'predict_decay': [1/x for x in [1*HOUR, 2*HOUR, 3*HOUR, 6*HOUR, 12*HOUR, 1*DAY, 7*DAY, 14*DAY]],
    }
)


pipe = builder.build()

In [16]:
pipe.run()

  0%|          | 0/15 [00:00<?, ?it/s]

/Users/robinverachtert/.virtualenvs/tars-item-knn/lib/python3.9/site-packages/scipy/sparse/_index.py:146: SparseEfficiencyWarning: Changing the sparsity structure of a csr_matrix is expensive. lil_matrix is more efficient.
  self._set_arrayXarray(i, j, x)


2022-07-13 10:10:45,884 - base - recpack - INFO - Fitting TARSItemKNNLee_W3 complete - Took 1.44e+02s


/Users/robinverachtert/.virtualenvs/tars-item-knn/lib/python3.9/site-packages/recpack/algorithms/base.py:274: UserWarning: TARSItemKNNLee_W3 missing similar items for 176 items.
  warnings.warn(f"{self.name} missing similar items for {missing} items.")
/Users/robinverachtert/.virtualenvs/tars-item-knn/lib/python3.9/site-packages/scipy/sparse/_index.py:146: SparseEfficiencyWarning: Changing the sparsity structure of a csr_matrix is expensive. lil_matrix is more efficient.
  self._set_arrayXarray(i, j, x)


2022-07-13 10:14:26,921 - base - recpack - INFO - Fitting TARSItemKNNLee_W3 complete - Took 1.66e+02s


...

/Users/robinverachtert/.virtualenvs/tars-item-knn/lib/python3.9/site-packages/recpack/algorithms/base.py:274: UserWarning: TARSItemKNNVaz missing similar items for 183 items.
  warnings.warn(f"{self.name} missing similar items for {missing} items.")
/Users/robinverachtert/.virtualenvs/tars-item-knn/lib/python3.9/site-packages/scipy/sparse/_index.py:146: SparseEfficiencyWarning: Changing the sparsity structure of a csr_matrix is expensive. lil_matrix is more efficient.
  self._set_arrayXarray(i, j, x)


2022-07-15 00:26:55,225 - base - recpack - INFO - Fitting TARSItemKNNVaz complete - Took 27.6s


/Users/robinverachtert/.virtualenvs/tars-item-knn/lib/python3.9/site-packages/recpack/algorithms/base.py:274: UserWarning: TARSItemKNNVaz missing similar items for 183 items.
  warnings.warn(f"{self.name} missing similar items for {missing} items.")
/Users/robinverachtert/.virtualenvs/tars-item-knn/lib/python3.9/site-packages/scipy/sparse/_index.py:146: SparseEfficiencyWarning: Changing the sparsity structure of a csr_matrix is expensive. lil_matrix is more efficient.
  self._set_arrayXarray(i, j, x)


2022-07-15 00:28:10,877 - base - recpack - INFO - Fitting TARSItemKNNVaz complete - Took 29.5s


/Users/robinverachtert/.virtualenvs/tars-item-knn/lib/python3.9/site-packages/recpack/algorithms/base.py:274: UserWarning: TARSItemKNNVaz missing similar items for 34 items.
  warnings.warn(f"{self.name} missing similar items for {missing} items.")


In [17]:
pipe.optimisation_results.sort_values('ndcgk_10', ascending=False)

identifier  \
1549  TARSItemKNN(K=10,decay_function=linear,fit_dec...   
2506  TARSItemKNN(K=10,decay_function=linear_steeper...   
1546  TARSItemKNN(K=10,decay_function=linear,fit_dec...   
1543  TARSItemKNN(K=10,decay_function=linear,fit_dec...   
2956  TARSItemKNN(K=500,decay_function=linear_steepe...   
...                                                 ...   
2351  TARSItemKNN(K=100,decay_function=convex,fit_de...   
2350  TARSItemKNN(K=100,decay_function=convex,fit_de...   
2349  TARSItemKNN(K=100,decay_function=convex,fit_de...   
2348  TARSItemKNN(K=100,decay_function=convex,fit_de...   
2342  TARSItemKNN(K=100,decay_function=convex,fit_de...   

                                                 params  ndcgk_10  
1549  {'K': 10, 'fit_decay': 1, 'predict_decay': 1, ...  0.044257  
2506  {'K': 10, 'fit_decay': 1, 'predict_decay': 1, ...  0.044257  
1546  {'K': 10, 'fit_decay': 1, 'predict_decay': 0.9...  0.044212  
1543  {'K': 10, 'fit_decay': 1, 'predict_decay': 0.7...  0.044182  
2956  {'K': 500, 'fit_decay': 2, 'predict_decay': 1,...  0.044175  
...                                                 ...       ...  
2351  {'K': 100, 'fit_decay': 0.3, 'predict_decay': ...  0.000000  
2350  {'K': 100, 'fit_decay': 0.3, 'predict_decay': ...  0.000000  
2349  {'K': 100, 'fit_decay': 0.3, 'predict_decay': ...  0.000000  
2348  {'K': 100, 'fit_decay': 0.3, 'predict_decay': ...  0.000000  
2342  {'K': 100, 'fit_decay': 0.1, 'predict_decay': ...  0.000000  

[3323 rows x 3 columns]

In [18]:
pipe.get_metrics().sort_values('ndcgk_10', ascending=False)

ndcgk_10  ndcgk_20  \
TARSItemKNN(K=500,decay_function=exponential,fi...  0.044908  0.049948   
TARSItemKNN(K=10,decay_function=concave,fit_dec...  0.043494  0.047115   
TARSItemKNN(K=10,decay_function=linear,fit_deca...  0.043478  0.047135   
TARSItemKNN(K=10,decay_function=linear_steeper,...  0.043478  0.047135   
TARSItemKNNDing(K=200,predict_decay=8.267195767...  0.042744  0.048272   
TARSItemKNN(K=500,decay_function=log,fit_decay=...  0.042359  0.047754   
ItemKNN(K=200,normalize=False,normalize_X=False...  0.041701  0.047161   
TARSItemKNNLee_W5(K=200,similarity=cosine)          0.034844  0.039303   
TARSItemKNNLee(K=200,W=3,similarity=cosine)         0.034797  0.039302   
TARSItemKNNLee_W3(K=200,similarity=cosine)          0.034749  0.039220   
TARSItemKNNLiu2012(K=200,decay=500)                 0.034202  0.038983   
TARSItemKNNLiu(K=200,fit_decay=8.26719576719576...  0.028669  0.031880   
TARSItemKNNVaz(K=500,fit_decay=8.26719576719576...  0.027756  0.030865   
Popularity(K=200)                                   0.022709  0.024600   
TARSItemKNN(K=50,decay_function=convex,fit_deca...  0.000053  0.000043   

                                                    ndcgk_50  coveragek_10  \
TARSItemKNN(K=500,decay_function=exponential,fi...  0.058614      0.407232   
TARSItemKNN(K=10,decay_function=concave,fit_dec...  0.051554      0.468300   
TARSItemKNN(K=10,decay_function=linear,fit_deca...  0.051553      0.468115   
TARSItemKNN(K=10,decay_function=linear_steeper,...  0.051553      0.468115   
TARSItemKNNDing(K=200,predict_decay=8.267195767...  0.057148      0.438173   
TARSItemKNN(K=500,decay_function=log,fit_decay=...  0.056831      0.392835   
ItemKNN(K=200,normalize=False,normalize_X=False...  0.056025      0.397350   
TARSItemKNNLee_W5(K=200,similarity=cosine)          0.047259      0.843703   
TARSItemKNNLee(K=200,W=3,similarity=cosine)         0.047298      0.840113   
TARSItemKNNLee_W3(K=200,similarity=cosine)          0.047343      0.837041   
TARSItemKNNLiu2012(K=200,decay=500)                 0.047064      0.827418   
TARSItemKNNLiu(K=200,fit_decay=8.26719576719576...  0.036861      0.900996   
TARSItemKNNVaz(K=500,fit_decay=8.26719576719576...  0.035897      0.898960   
Popularity(K=200)                                   0.030411      0.001925   
TARSItemKNN(K=50,decay_function=convex,fit_deca...  0.000037      0.009105   

                                                    coveragek_20  
TARSItemKNN(K=500,decay_function=exponential,fi...      0.548577  
TARSItemKNN(K=10,decay_function=concave,fit_dec...      0.591658  
TARSItemKNN(K=10,decay_function=linear,fit_deca...      0.591658  
TARSItemKNN(K=10,decay_function=linear_steeper,...      0.591658  
TARSItemKNNDing(K=200,predict_decay=8.267195767...      0.580443  
TARSItemKNN(K=500,decay_function=log,fit_decay=...      0.529886  
ItemKNN(K=200,normalize=False,normalize_X=False...      0.539139  
TARSItemKNNLee_W5(K=200,similarity=cosine)              0.946075  
TARSItemKNNLee(K=200,W=3,similarity=cosine)             0.943743  
TARSItemKNNLee_W3(K=200,similarity=cosine)              0.941338  
TARSItemKNNLiu2012(K=200,decay=500)                     0.934565  
TARSItemKNNLiu(K=200,fit_decay=8.26719576719576...      0.966135  
TARSItemKNNVaz(K=500,fit_decay=8.26719576719576...      0.964729  
Popularity(K=200)                                       0.003035  
TARSItemKNN(K=50,decay_function=convex,fit_deca...      0.009808

In [19]:
pipe.save_metrics()

In [ ]:
# TODO: experiment with Hermann2010
# TODO: experiment with Anelli2019
# TODO: experiment with generalization of Hermann and Xia

In [8]:
builder = PipelineBuilder(f'experiment_{DATASET}_extensions_12_07')
builder.set_data_from_scenario(scenario)
builder.set_optimisation_metric('NDCGK', 10)
builder.add_metric('NDCGK', [10, 20, 50])
builder.add_metric('CoverageK', [10, 20])

# builder.add_algorithm(
#     'TARSUserKNNAnelli',
#     grid={
#         'decay': [1/x for x in [1*HOUR, 2*HOUR, 3*HOUR, 6*HOUR, 12*HOUR, 1*DAY, 7*DAY, 14*DAY]],
#     }
# )

pipe = builder.build()

In [ ]:
builder = PipelineBuilder(f'experiment_{DATASET}_baselines')
builder.set_data_from_scenario(scenario)
builder.set_optimisation_metric('NDCGK', 10)
builder.add_metric('NDCGK', [10, 20, 50])
builder.add_metric('CoverageK', [10, 20])

builder.add_algorithm('ItemKNN', grid={'similarity': ['cosine', 'conditional_probability']})
builder.add_algorithm('Popularity')


pipe = builder.build()

In [13]:
pipe.run()

  0%|          | 0/2 [00:00<?, ?it/s]

/Users/robinverachtert/.virtualenvs/tars-item-knn/lib/python3.9/site-packages/scipy/sparse/_index.py:146: SparseEfficiencyWarning: Changing the sparsity structure of a csr_matrix is expensive. lil_matrix is more efficient.
  self._set_arrayXarray(i, j, x)


2022-07-08 15:07:48,996 - base - recpack - INFO - Fitting ItemKNN complete - Took 19.5s


/Users/robinverachtert/.virtualenvs/tars-item-knn/lib/python3.9/site-packages/recpack/algorithms/base.py:274: UserWarning: ItemKNN missing similar items for 1490 items.
  warnings.warn(f"{self.name} missing similar items for {missing} items.")
/Users/robinverachtert/.virtualenvs/tars-item-knn/lib/python3.9/site-packages/scipy/sparse/_index.py:146: SparseEfficiencyWarning: Changing the sparsity structure of a csr_matrix is expensive. lil_matrix is more efficient.
  self._set_arrayXarray(i, j, x)


2022-07-08 15:08:06,758 - base - recpack - INFO - Fitting ItemKNN complete - Took 16.8s


/Users/robinverachtert/.virtualenvs/tars-item-knn/lib/python3.9/site-packages/recpack/algorithms/base.py:274: UserWarning: ItemKNN missing similar items for 1490 items.
  warnings.warn(f"{self.name} missing similar items for {missing} items.")
/Users/robinverachtert/.virtualenvs/tars-item-knn/lib/python3.9/site-packages/scipy/sparse/_index.py:146: SparseEfficiencyWarning: Changing the sparsity structure of a csr_matrix is expensive. lil_matrix is more efficient.
  self._set_arrayXarray(i, j, x)


2022-07-08 15:08:30,577 - base - recpack - INFO - Fitting ItemKNN complete - Took 22.6s


/Users/robinverachtert/.virtualenvs/tars-item-knn/lib/python3.9/site-packages/recpack/algorithms/base.py:274: UserWarning: ItemKNN missing similar items for 709 items.
  warnings.warn(f"{self.name} missing similar items for {missing} items.")


2022-07-08 15:08:41,341 - base - recpack - INFO - Fitting Popularity complete - Took 9.03s


In [14]:
pipe.get_metrics()

ndcgk_10  ndcgk_20  \
ItemKNN(K=200,normalize=False,normalize_X=False...  0.163931  0.178267   
Popularity(K=200)                                   0.001316  0.002829   

                                                    ndcgk_50  coveragek_10  \
ItemKNN(K=200,normalize=False,normalize_X=False...  0.208204      0.026314   
Popularity(K=200)                                   0.006755      0.000290   

                                                    coveragek_20  
ItemKNN(K=200,normalize=False,normalize_X=False...      0.044858  
Popularity(K=200)                                       0.000553

In [15]:
pipe.save_metrics()

In [16]:
from recpack.algorithms import TARSItemKNN

In [17]:
builder = PipelineBuilder(f'experiment_{DATASET}_masterclass')
builder.set_data_from_scenario(scenario)
builder.set_optimisation_metric('NDCGK', 10)
builder.add_metric('NDCGK', [10, 20, 50])
builder.add_metric('RecallK', [10, 20, 50])
builder.add_metric('CoverageK', [10, 20])

builder.add_algorithm(
    'TARSItemKNN', 
    params={'decay_function': 'exponential'},
    grid={
        'similarity': TARSItemKNN.SUPPORTED_SIMILARITIES,
        'K': [10, 50, 100, 200, 500],
        'fit_decay': [1/x for x in [3600, 7200, 36000, 72000]],
        'predict_decay': [1/x for x in [3600, 7200, 36000, 72000]]
    }
)
builder.add_algorithm(
    'TARSItemKNN', 
    params={'decay_function': 'log'},
    grid={
        'similarity': TARSItemKNN.SUPPORTED_SIMILARITIES,
        'K': [10, 50, 100, 200, 500],
        'fit_decay': [2, 4, 8, 16, 32],
        'predict_decay': [2, 4, 8, 16, 32]
    }
)
builder.add_algorithm(
    'TARSItemKNN', 
    params={'decay_function': 'linear'},
    grid={
        'similarity': TARSItemKNN.SUPPORTED_SIMILARITIES,
        'K': [10, 50, 100, 200, 500],
        'fit_decay': [0.1, 0.3, 0.5, 0.8, 1],
        'predict_decay': [0.1, 0.3, 0.5, 0.8, 1],
    }
)
builder.add_algorithm(
    'TARSItemKNN', 
    params={'decay_function': 'concave'},
    grid={
        'similarity': TARSItemKNN.SUPPORTED_SIMILARITIES,
        'K': [10, 50, 100, 200, 500],
        'fit_decay': [0.01, 0.1, 0.3, 0.9],
        'predict_decay': [0.01, 0.1, 0.3, 0.9]
    }
)
builder.add_algorithm(
    'TARSItemKNN', 
    params={'decay_function': 'convex'},
    grid={
        'similarity': TARSItemKNN.SUPPORTED_SIMILARITIES,
        'K': [10, 50, 100, 200, 500],
        'fit_decay': [0.01, 0.1, 0.3, 0.9],
        'predict_decay': [0.01, 0.1, 0.3, 0.9]
    }
)

pipe = builder.build()

In [18]:
pipe.run()

  0%|          | 0/5 [00:00<?, ?it/s]

/Users/robinverachtert/.virtualenvs/tars-item-knn/lib/python3.9/site-packages/scipy/sparse/_index.py:146: SparseEfficiencyWarning: Changing the sparsity structure of a csr_matrix is expensive. lil_matrix is more efficient.
  self._set_arrayXarray(i, j, x)


2022-07-08 15:09:39,851 - base - recpack - INFO - Fitting TARSItemKNN complete - Took 39.3s


/Users/robinverachtert/.virtualenvs/tars-item-knn/lib/python3.9/site-packages/recpack/algorithms/base.py:274: UserWarning: TARSItemKNN missing similar items for 11744 items.
  warnings.warn(f"{self.name} missing similar items for {missing} items.")
/Users/robinverachtert/.virtualenvs/tars-item-knn/lib/python3.9/site-packages/scipy/sparse/_index.py:146: SparseEfficiencyWarning: Changing the sparsity structure of a csr_matrix is expensive. lil_matrix is more efficient.
  self._set_arrayXarray(i, j, x)


2022-07-08 15:10:21,259 - base - recpack - INFO - Fitting TARSItemKNN complete - Took 40.6s


...

/Users/robinverachtert/.virtualenvs/tars-item-knn/lib/python3.9/site-packages/recpack/algorithms/base.py:274: UserWarning: TARSItemKNN missing similar items for 33231 items.
  warnings.warn(f"{self.name} missing similar items for {missing} items.")
/Users/robinverachtert/.virtualenvs/tars-item-knn/lib/python3.9/site-packages/recpack/algorithms/base.py:122: UserWarning: TARSItemKNN failed to recommend any items for 20 users
  warnings.warn(f"{self.name} failed to recommend any items " f"for {len(missing)} users")
/Users/robinverachtert/.virtualenvs/tars-item-knn/lib/python3.9/site-packages/scipy/sparse/_index.py:146: SparseEfficiencyWarning: Changing the sparsity structure of a csr_matrix is expensive. lil_matrix is more efficient.
  self._set_arrayXarray(i, j, x)


2022-07-09 04:43:44,214 - base - recpack - INFO - Fitting TARSItemKNN complete - Took 20.9s


/Users/robinverachtert/.virtualenvs/tars-item-knn/lib/python3.9/site-packages/recpack/algorithms/base.py:274: UserWarning: TARSItemKNN missing similar items for 35993 items.
  warnings.warn(f"{self.name} missing similar items for {missing} items.")
/Users/robinverachtert/.virtualenvs/tars-item-knn/lib/python3.9/site-packages/recpack/algorithms/base.py:122: UserWarning: TARSItemKNN failed to recommend any items for 23 users
  warnings.warn(f"{self.name} failed to recommend any items " f"for {len(missing)} users")
/Users/robinverachtert/.virtualenvs/tars-item-knn/lib/python3.9/site-packages/scipy/sparse/_index.py:146: SparseEfficiencyWarning: Changing the sparsity structure of a csr_matrix is expensive. lil_matrix is more efficient.
  self._set_arrayXarray(i, j, x)


2022-07-09 04:44:15,991 - base - recpack - INFO - Fitting TARSItemKNN complete - Took 31.2s


/Users/robinverachtert/.virtualenvs/tars-item-knn/lib/python3.9/site-packages/recpack/algorithms/base.py:274: UserWarning: TARSItemKNN missing similar items for 35031 items.
  warnings.warn(f"{self.name} missing similar items for {missing} items.")
/Users/robinverachtert/.virtualenvs/tars-item-knn/lib/python3.9/site-packages/recpack/algorithms/base.py:122: UserWarning: TARSItemKNN failed to recommend any items for 21 users
  warnings.warn(f"{self.name} failed to recommend any items " f"for {len(missing)} users")


In [22]:
pipe.get_metrics().sort_values('ndcgk_10', ascending=False)

ndcgk_10  ndcgk_20  \
TARSItemKNN(K=50,decay_function=concave,fit_dec...  0.170098  0.185695   
TARSItemKNN(K=500,decay_function=linear,fit_dec...  0.169586  0.185108   
TARSItemKNN(K=200,decay_function=log,fit_decay=...  0.166903  0.182343   
TARSItemKNN(K=10,decay_function=exponential,fit...  0.163051  0.174361   
TARSItemKNN(K=10,decay_function=convex,fit_deca...  0.067913  0.075759   

                                                    ndcgk_50  recallk_10  \
TARSItemKNN(K=50,decay_function=concave,fit_dec...  0.216238    0.228176   
TARSItemKNN(K=500,decay_function=linear,fit_dec...  0.213849    0.227436   
TARSItemKNN(K=200,decay_function=log,fit_decay=...  0.211075    0.224811   
TARSItemKNN(K=10,decay_function=exponential,fit...  0.179599    0.220360   
TARSItemKNN(K=10,decay_function=convex,fit_deca...  0.077248    0.099721   

                                                    recallk_20  recallk_50  \
TARSItemKNN(K=50,decay_function=concave,fit_dec...    0.271728    0.386527   
TARSItemKNN(K=500,decay_function=linear,fit_dec...    0.270247    0.377087   
TARSItemKNN(K=200,decay_function=log,fit_decay=...    0.265797    0.373273   
TARSItemKNN(K=10,decay_function=exponential,fit...    0.256753    0.273145   
TARSItemKNN(K=10,decay_function=convex,fit_deca...    0.125902    0.131791   

                                                    coveragek_10  coveragek_20  
TARSItemKNN(K=50,decay_function=concave,fit_dec...      0.025129      0.042224  
TARSItemKNN(K=500,decay_function=linear,fit_dec...      0.025182      0.042066  
TARSItemKNN(K=200,decay_function=log,fit_decay=...      0.025709      0.043884  
TARSItemKNN(K=10,decay_function=exponential,fit...      0.021441      0.027974  
TARSItemKNN(K=10,decay_function=convex,fit_deca...      0.015462      0.018728

In [20]:
pipe.optimisation_results.sort_values('ndcgk_10', ascending=False)

identifier  \
37    TARSItemKNN(K=10,decay_function=exponential,fi...   
40    TARSItemKNN(K=10,decay_function=exponential,fi...   
229   TARSItemKNN(K=500,decay_function=exponential,f...   
181   TARSItemKNN(K=200,decay_function=exponential,f...   
85    TARSItemKNN(K=50,decay_function=exponential,fi...   
...                                                 ...   
1230  TARSItemKNN(K=10,decay_function=convex,fit_dec...   
1326  TARSItemKNN(K=100,decay_function=convex,fit_de...   
1422  TARSItemKNN(K=500,decay_function=convex,fit_de...   
1278  TARSItemKNN(K=50,decay_function=convex,fit_dec...   
1374  TARSItemKNN(K=200,decay_function=convex,fit_de...   

                                                 params  ndcgk_10  
37    {'K': 10, 'fit_decay': 1.388888888888889e-05, ...  0.156035  
40    {'K': 10, 'fit_decay': 1.388888888888889e-05, ...  0.155614  
229   {'K': 500, 'fit_decay': 1.388888888888889e-05,...  0.155541  
181   {'K': 200, 'fit_decay': 1.388888888888889e-05,...  0.155541  
85    {'K': 50, 'fit_decay': 1.388888888888889e-05, ...  0.155541  
...                                                 ...       ...  
1230  {'K': 10, 'fit_decay': 0.01, 'predict_decay': ...  0.019176  
1326  {'K': 100, 'fit_decay': 0.01, 'predict_decay':...  0.019176  
1422  {'K': 500, 'fit_decay': 0.01, 'predict_decay':...  0.019176  
1278  {'K': 50, 'fit_decay': 0.01, 'predict_decay': ...  0.019176  
1374  {'K': 200, 'fit_decay': 0.01, 'predict_decay':...  0.019176  

[1470 rows x 3 columns]

In [21]:
pipe.save_metrics()